In [1]:
import os
import copy
import time
import pickle
import numpy as np
import easydict
from tqdm import tqdm

import torch
from tensorboardX import SummaryWriter

from options import args_parser
from update import LocalUpdate, test_inference
from models import MLP, CNNMnist, CNNFashion_Mnist, CNNCifar, CNNCifar_fedVC, CNNCifar_VCBN, CNNCifar_VCGN, CNNCifar_WS
from utils import get_dataset, average_weights, exp_details, get_logger, CSVLogger
from fed_cifar100 import load_partition_data_federated_cifar100
from resnet_gn import resnet18
from resnet import ResNet32_test
from vgg import vgg11_bn, vgg11
import random
import logging
import datetime

from test import main_test

In [2]:
loss_list = [[] for i in range(0, 10)]
val_acc_list = [[] for i in range(0, 10)]
batch_loss_list = [[] for i in range(0, 10)]
conv_grad_list = [[] for i in range(0, 10)]
fc_grad_list = [[] for i in range(0, 10)]
total_grad_list = [[] for i in range(0, 10)]

## 기본 1

In [3]:
args = easydict.EasyDict({
    "model": 'resnet18',
    'dataset': 'cifar100',
    'gpu': 0,
    'iid': 2,
    'epochs': 4000,
    'optimizer': 'no_weight_decay',
    'seed': 0,
    'norm': 'group_norm',
    'num_users': 500,
    'frac': 0.02,
    'local_ep': 1,
    'local_bs': 20,
    'lr': 0.1,
    'momentum': 0,
    'kernel_num': 9,
    'kernel_sizes': '3,4,5',
    'num_channnels': '1',
    'num_filters': 32,
    'max_pool': 'True',
    'num_classes': 100,
    'unequal': 0,
    'stopping_rounds': 10,
    'verbose': 0,
    'hold_normalize': 0,
    'save_path': '../save/checkpoint',
    'exp_folder': 'fedopt_frac0.02',
    'resume': None,
    'lr_decay': 1
})

loss_list[0], val_acc_list[0], batch_loss_list[0], conv_grad_list[0], fc_grad_list[0], total_grad_list[0] = main_test(args)

INFO:root:{'model': 'resnet18', 'dataset': 'cifar100', 'gpu': 0, 'iid': 2, 'epochs': 4000, 'optimizer': 'no_weight_decay', 'seed': 0, 'norm': 'group_norm', 'num_users': 500, 'frac': 0.02, 'local_ep': 1, 'local_bs': 20, 'lr': 0.1, 'momentum': 0, 'kernel_num': 9, 'kernel_sizes': '3,4,5', 'num_channnels': '1', 'num_filters': 32, 'max_pool': 'True', 'num_classes': 100, 'unequal': 0, 'stopping_rounds': 10, 'verbose': 0, 'hold_normalize': 0, 'save_path': '../save/checkpoint\\fedopt_frac0.02', 'exp_folder': 'fedopt_frac0.02', 'resume': None, 'lr_decay': 1}
INFO:root:ResNet(
  (conv1): Conv2d(3, 64, kernel_size=(7, 7), stride=(2, 2), padding=(3, 3), bias=False)
  (bn1): GroupNorm2d(2, eps=1e-05, momentum=0.1, affine=True, track_running_stats=False)
  (relu): ReLU(inplace=True)
  (maxpool): MaxPool2d(kernel_size=3, stride=2, padding=1, dilation=1, ceil_mode=False)
  (layer1): Sequential(
    (0): BasicBlock(
      (conv1): Conv2d(64, 64, kernel_size=(3, 3), stride=(1, 1), padding=(1, 1), bias=F

num_channels_per_group:32
num_channels_per_group:32
num_channels_per_group:32
num_channels_per_group:32
num_channels_per_group:32
num_channels_per_group:64
num_channels_per_group:64
num_channels_per_group:64
num_channels_per_group:64
num_channels_per_group:64
num_channels_per_group:128
num_channels_per_group:128
num_channels_per_group:128
num_channels_per_group:128
num_channels_per_group:128
num_channels_per_group:256
num_channels_per_group:256
num_channels_per_group:256
num_channels_per_group:256
num_channels_per_group:256


  0%|                                                                                         | 0/4000 [00:00<?, ?it/s]INFO:root: 
Avg Training Stats after 1 global rounds:
INFO:root:Training Loss : 4.136322169303894
INFO:root:Train Accuracy: 0.86% 

  0%|                                                                               | 1/4000 [00:03<3:48:22,  3.43s/it]INFO:root: 
Avg Training Stats after 2 global rounds:
INFO:root:Training Loss : 3.9643336534500113
INFO:root:Train Accuracy: 0.70% 

  0%|                                                                               | 2/4000 [00:05<2:53:29,  2.60s/it]INFO:root: 
Avg Training Stats after 3 global rounds:
INFO:root:Training Loss : 3.9782898855209354
INFO:root:Train Accuracy: 1.15% 

  0%|                                                                               | 3/4000 [00:07<2:33:42,  2.31s/it]INFO:root: 
Avg Training Stats after 4 global rounds:
INFO:root:Training Loss : 4.0448313093185435
INFO:root:Train Accuracy: 1

  1%|▌                                                                             | 32/4000 [01:04<2:07:18,  1.93s/it]INFO:root: 
Avg Training Stats after 33 global rounds:
INFO:root:Training Loss : 3.717012462615967
INFO:root:Train Accuracy: 4.34% 

  1%|▋                                                                             | 33/4000 [01:06<2:07:17,  1.93s/it]INFO:root: 
Avg Training Stats after 34 global rounds:
INFO:root:Training Loss : 3.8074392890930175
INFO:root:Train Accuracy: 4.48% 

  1%|▋                                                                             | 34/4000 [01:08<2:07:15,  1.93s/it]INFO:root: 
Avg Training Stats after 35 global rounds:
INFO:root:Training Loss : 3.76670006275177
INFO:root:Train Accuracy: 4.88% 

  1%|▋                                                                             | 35/4000 [01:10<2:07:25,  1.93s/it]INFO:root: 
Avg Training Stats after 36 global rounds:
INFO:root:Training Loss : 3.5961403226852418
INFO:root:Train Accuracy:

  2%|█▏                                                                            | 64/4000 [02:06<2:07:14,  1.94s/it]INFO:root: 
Avg Training Stats after 65 global rounds:
INFO:root:Training Loss : 3.4345424461364744
INFO:root:Train Accuracy: 6.91% 

  2%|█▎                                                                            | 65/4000 [02:08<2:07:07,  1.94s/it]INFO:root: 
Avg Training Stats after 66 global rounds:
INFO:root:Training Loss : 3.4026493787765504
INFO:root:Train Accuracy: 7.14% 

  2%|█▎                                                                            | 66/4000 [02:10<2:07:15,  1.94s/it]INFO:root: 
Avg Training Stats after 67 global rounds:
INFO:root:Training Loss : 3.4233798217773432
INFO:root:Train Accuracy: 6.54% 

  2%|█▎                                                                            | 67/4000 [02:12<2:07:14,  1.94s/it]INFO:root: 
Avg Training Stats after 68 global rounds:
INFO:root:Training Loss : 3.4905616903305052
INFO:root:Train Accura

...

INFO:root:Training Loss : 0.0001742314549483126
INFO:root:Train Accuracy: 29.96% 

 98%|██████████████████████████████████████████████████████████████████████████▎ | 3914/4000 [3:23:10<06:52,  4.80s/it]INFO:root: 
Avg Training Stats after 3915 global rounds:
INFO:root:Training Loss : 0.000131341578962747
INFO:root:Train Accuracy: 29.97% 

 98%|██████████████████████████████████████████████████████████████████████████▍ | 3915/4000 [3:23:15<06:47,  4.80s/it]INFO:root: 
Avg Training Stats after 3916 global rounds:
INFO:root:Training Loss : 0.00014227386523998575
INFO:root:Train Accuracy: 29.97% 

 98%|██████████████████████████████████████████████████████████████████████████▍ | 3916/4000 [3:23:20<06:49,  4.87s/it]INFO:root: 
Avg Training Stats after 3917 global rounds:
INFO:root:Training Loss : 0.00012591526974574662
INFO:root:Train Accuracy: 29.95% 

 98%|██████████████████████████████████████████████████████████████████████████▍ | 3917/4000 [3:23:25<06:47,  4.90s/it]INFO:root: 
Avg Trai

 99%|██████████████████████████████████████████████████████████████████████████▉ | 3945/4000 [3:25:43<04:28,  4.88s/it]INFO:root: 
Avg Training Stats after 3946 global rounds:
INFO:root:Training Loss : 0.00013718635469558648
INFO:root:Train Accuracy: 30.02% 

 99%|██████████████████████████████████████████████████████████████████████████▉ | 3946/4000 [3:25:48<04:23,  4.87s/it]INFO:root: 
Avg Training Stats after 3947 global rounds:
INFO:root:Training Loss : 0.00012844644574215637
INFO:root:Train Accuracy: 30.04% 

 99%|██████████████████████████████████████████████████████████████████████████▉ | 3947/4000 [3:25:53<04:17,  4.85s/it]INFO:root: 
Avg Training Stats after 3948 global rounds:
INFO:root:Training Loss : 0.0001440670542069711
INFO:root:Train Accuracy: 30.01% 

 99%|███████████████████████████████████████████████████████████████████████████ | 3948/4000 [3:25:58<04:15,  4.91s/it]INFO:root: 
Avg Training Stats after 3949 global rounds:
INFO:root:Training Loss : 0.00014424800305278

INFO:root:Training Loss : 0.00014874259381031152
INFO:root:Train Accuracy: 30.01% 

 99%|███████████████████████████████████████████████████████████████████████████▌| 3977/4000 [3:28:21<01:52,  4.89s/it]INFO:root: 
Avg Training Stats after 3978 global rounds:
INFO:root:Training Loss : 0.00012856302695581686
INFO:root:Train Accuracy: 30.02% 

 99%|███████████████████████████████████████████████████████████████████████████▌| 3978/4000 [3:28:26<01:48,  4.92s/it]INFO:root: 
Avg Training Stats after 3979 global rounds:
INFO:root:Training Loss : 0.00013033313734922558
INFO:root:Train Accuracy: 30.03% 

 99%|███████████████████████████████████████████████████████████████████████████▌| 3979/4000 [3:28:31<01:43,  4.92s/it]INFO:root: 
Avg Training Stats after 3980 global rounds:
INFO:root:Training Loss : 0.00011500435728521553
INFO:root:Train Accuracy: 30.03% 

100%|███████████████████████████████████████████████████████████████████████████▌| 3980/4000 [3:28:36<01:37,  4.87s/it]INFO:root: 
Avg T

 Saving checkpoints to ../save/checkpoint\fedopt_frac0.02\cifar100_resnet18_T[4000]_C[0.02]_iid[2]_E[1]_B[20]...


INFO:root: 
 Results after 4000 global rounds of training:
INFO:root:|---- Test Accuracy: 30.00%


## 기본 0.1

In [4]:
args = easydict.EasyDict({
    "model": 'resnet18',
    'dataset': 'cifar100',
    'gpu': 0,
    'iid': 2,
    'epochs': 4000,
    'optimizer': 'no_weight_decay',
    'seed': 0,
    'norm': 'group_norm',
    'num_users': 500,
    'frac': 0.02,
    'local_ep': 1,
    'local_bs': 20,
    'lr': 0.01,
    'momentum': 0,
    'kernel_num': 9,
    'kernel_sizes': '3,4,5',
    'num_channnels': '1',
    'num_filters': 32,
    'max_pool': 'True',
    'num_classes': 100,
    'unequal': 0,
    'stopping_rounds': 10,
    'verbose': 0,
    'hold_normalize': 0,
    'save_path': '../save/checkpoint',
    'exp_folder': 'fedopt_frac0.02',
    'resume': None,
    'lr_decay': 1
})

loss_list[1], val_acc_list[1], batch_loss_list[1], conv_grad_list[1], fc_grad_list[1], total_grad_list[1] = main_test(args)

INFO:root:{'model': 'resnet18', 'dataset': 'cifar100', 'gpu': 0, 'iid': 2, 'epochs': 4000, 'optimizer': 'no_weight_decay', 'seed': 0, 'norm': 'group_norm', 'num_users': 500, 'frac': 0.02, 'local_ep': 1, 'local_bs': 20, 'lr': 0.01, 'momentum': 0, 'kernel_num': 9, 'kernel_sizes': '3,4,5', 'num_channnels': '1', 'num_filters': 32, 'max_pool': 'True', 'num_classes': 100, 'unequal': 0, 'stopping_rounds': 10, 'verbose': 0, 'hold_normalize': 0, 'save_path': '../save/checkpoint\\fedopt_frac0.02', 'exp_folder': 'fedopt_frac0.02', 'resume': None, 'lr_decay': 1}
INFO:root:ResNet(
  (conv1): Conv2d(3, 64, kernel_size=(7, 7), stride=(2, 2), padding=(3, 3), bias=False)
  (bn1): GroupNorm2d(2, eps=1e-05, momentum=0.1, affine=True, track_running_stats=False)
  (relu): ReLU(inplace=True)
  (maxpool): MaxPool2d(kernel_size=3, stride=2, padding=1, dilation=1, ceil_mode=False)
  (layer1): Sequential(
    (0): BasicBlock(
      (conv1): Conv2d(64, 64, kernel_size=(3, 3), stride=(1, 1), padding=(1, 1), bias=

num_channels_per_group:32
num_channels_per_group:32
num_channels_per_group:32
num_channels_per_group:32
num_channels_per_group:32
num_channels_per_group:64
num_channels_per_group:64
num_channels_per_group:64
num_channels_per_group:64
num_channels_per_group:64
num_channels_per_group:128
num_channels_per_group:128
num_channels_per_group:128
num_channels_per_group:128
num_channels_per_group:128
num_channels_per_group:256
num_channels_per_group:256
num_channels_per_group:256
num_channels_per_group:256
num_channels_per_group:256


  0%|                                                                                         | 0/4000 [00:00<?, ?it/s]INFO:root: 
Avg Training Stats after 1 global rounds:
INFO:root:Training Loss : 4.324650111198426
INFO:root:Train Accuracy: 0.96% 

  0%|                                                                               | 1/4000 [00:02<2:28:18,  2.23s/it]INFO:root: 
Avg Training Stats after 2 global rounds:
INFO:root:Training Loss : 4.325459213256836
INFO:root:Train Accuracy: 0.95% 

  0%|                                                                               | 2/4000 [00:04<2:27:16,  2.21s/it]INFO:root: 
Avg Training Stats after 3 global rounds:
INFO:root:Training Loss : 4.3392231035232545
INFO:root:Train Accuracy: 1.08% 

  0%|                                                                               | 3/4000 [00:06<2:27:39,  2.22s/it]INFO:root: 
Avg Training Stats after 4 global rounds:
INFO:root:Training Loss : 4.312036056518555
INFO:root:Train Accuracy: 1.4

INFO:root:Training Loss : 3.7140239334106453
INFO:root:Train Accuracy: 2.39% 

  1%|▋                                                                             | 33/4000 [01:12<2:24:04,  2.18s/it]INFO:root: 
Avg Training Stats after 34 global rounds:
INFO:root:Training Loss : 3.9134365749359135
INFO:root:Train Accuracy: 2.32% 

  1%|▋                                                                             | 34/4000 [01:14<2:23:36,  2.17s/it]INFO:root: 
Avg Training Stats after 35 global rounds:
INFO:root:Training Loss : 3.8336359691619877
INFO:root:Train Accuracy: 2.54% 

  1%|▋                                                                             | 35/4000 [01:16<2:23:45,  2.18s/it]INFO:root: 
Avg Training Stats after 36 global rounds:
INFO:root:Training Loss : 3.7424786043167115
INFO:root:Train Accuracy: 2.85% 

  1%|▋                                                                             | 36/4000 [01:19<2:23:33,  2.17s/it]INFO:root: 
Avg Training Stats after 37 glo

  2%|█▎                                                                            | 65/4000 [02:21<2:20:18,  2.14s/it]INFO:root: 
Avg Training Stats after 66 global rounds:
INFO:root:Training Loss : 3.4309609127044673
INFO:root:Train Accuracy: 4.56% 

  2%|█▎                                                                            | 66/4000 [02:23<2:20:22,  2.14s/it]INFO:root: 
Avg Training Stats after 67 global rounds:
INFO:root:Training Loss : 3.603096265792847
INFO:root:Train Accuracy: 3.43% 

  2%|█▎                                                                            | 67/4000 [02:25<2:19:59,  2.14s/it]INFO:root: 
Avg Training Stats after 68 global rounds:
INFO:root:Training Loss : 3.628765602111816
INFO:root:Train Accuracy: 4.55% 

  2%|█▎                                                                            | 68/4000 [02:27<2:20:13,  2.14s/it]INFO:root: 
Avg Training Stats after 69 global rounds:
INFO:root:Training Loss : 3.669877309799195
INFO:root:Train Accuracy:

...

 98%|██████████████████████████████████████████████████████████████████████████▋ | 3931/4000 [3:30:19<05:37,  4.89s/it]INFO:root: 
Avg Training Stats after 3932 global rounds:
INFO:root:Training Loss : 0.004880958306603133
INFO:root:Train Accuracy: 29.83% 

 98%|██████████████████████████████████████████████████████████████████████████▋ | 3932/4000 [3:30:24<05:31,  4.87s/it]INFO:root: 
Avg Training Stats after 3933 global rounds:
INFO:root:Training Loss : 0.004667714829556644
INFO:root:Train Accuracy: 29.69% 

 98%|██████████████████████████████████████████████████████████████████████████▋ | 3933/4000 [3:30:29<05:23,  4.83s/it]INFO:root: 
Avg Training Stats after 3934 global rounds:
INFO:root:Training Loss : 0.004827573481015862
INFO:root:Train Accuracy: 29.74% 

 98%|██████████████████████████████████████████████████████████████████████████▋ | 3934/4000 [3:30:34<05:21,  4.88s/it]INFO:root: 
Avg Training Stats after 3935 global rounds:
INFO:root:Training Loss : 0.004715578239411115
INF

INFO:root:Train Accuracy: 29.76% 

 99%|███████████████████████████████████████████████████████████████████████████▎| 3963/4000 [3:32:53<02:59,  4.85s/it]INFO:root: 
Avg Training Stats after 3964 global rounds:
INFO:root:Training Loss : 0.004578353371471167
INFO:root:Train Accuracy: 29.76% 

 99%|███████████████████████████████████████████████████████████████████████████▎| 3964/4000 [3:32:58<02:58,  4.96s/it]INFO:root: 
Avg Training Stats after 3965 global rounds:
INFO:root:Training Loss : 0.004870418962091208
INFO:root:Train Accuracy: 29.78% 

 99%|███████████████████████████████████████████████████████████████████████████▎| 3965/4000 [3:33:03<02:54,  4.97s/it]INFO:root: 
Avg Training Stats after 3966 global rounds:
INFO:root:Training Loss : 0.004914166321977972
INFO:root:Train Accuracy: 29.81% 

 99%|███████████████████████████████████████████████████████████████████████████▎| 3966/4000 [3:33:08<02:46,  4.89s/it]INFO:root: 
Avg Training Stats after 3967 global rounds:
INFO:root:Train

INFO:root:Training Loss : 0.004437400214374066
INFO:root:Train Accuracy: 29.73% 

100%|███████████████████████████████████████████████████████████████████████████▉| 3995/4000 [3:35:29<00:23,  4.78s/it]INFO:root: 
Avg Training Stats after 3996 global rounds:
INFO:root:Training Loss : 0.004255206743255259
INFO:root:Train Accuracy: 29.87% 

100%|███████████████████████████████████████████████████████████████████████████▉| 3996/4000 [3:35:33<00:19,  4.79s/it]INFO:root: 
Avg Training Stats after 3997 global rounds:
INFO:root:Training Loss : 0.0042583462875336415
INFO:root:Train Accuracy: 29.76% 

100%|███████████████████████████████████████████████████████████████████████████▉| 3997/4000 [3:35:38<00:14,  4.82s/it]INFO:root: 
Avg Training Stats after 3998 global rounds:
INFO:root:Training Loss : 0.005050074127502739
INFO:root:Train Accuracy: 29.69% 

100%|███████████████████████████████████████████████████████████████████████████▉| 3998/4000 [3:35:43<00:09,  4.85s/it]INFO:root: 
Avg Training

 Saving checkpoints to ../save/checkpoint\fedopt_frac0.02\cifar100_resnet18_T[4000]_C[0.02]_iid[2]_E[1]_B[20]...


INFO:root: 
 Results after 4000 global rounds of training:
INFO:root:|---- Test Accuracy: 29.71%


## ws+gn 1

In [5]:
args = easydict.EasyDict({
    "model": 'resnet18_ws',
    'dataset': 'cifar100',
    'gpu': 0,
    'iid': 2,
    'epochs': 4000,
    'optimizer': 'no_weight_decay',
    'seed': 0,
    'norm': 'group_norm',
    'num_users': 500,
    'frac': 0.02,
    'local_ep': 1,
    'local_bs': 20,
    'lr': 1,
    'momentum': 0,
    'kernel_num': 9,
    'kernel_sizes': '3,4,5',
    'num_channnels': '1',
    'num_filters': 32,
    'max_pool': 'True',
    'num_classes': 100,
    'unequal': 0,
    'stopping_rounds': 10,
    'verbose': 0,
    'hold_normalize': 0,
    'save_path': '../save/checkpoint',
    'exp_folder': 'fedopt_frac0.02',
    'resume': None,
    'lr_decay': 1
})

loss_list[2], val_acc_list[2], batch_loss_list[2], conv_grad_list[2], fc_grad_list[2], total_grad_list[2] = main_test(args)

INFO:root:{'model': 'resnet18_ws', 'dataset': 'cifar100', 'gpu': 0, 'iid': 2, 'epochs': 4000, 'optimizer': 'no_weight_decay', 'seed': 0, 'norm': 'group_norm', 'num_users': 500, 'frac': 0.02, 'local_ep': 1, 'local_bs': 20, 'lr': 1, 'momentum': 0, 'kernel_num': 9, 'kernel_sizes': '3,4,5', 'num_channnels': '1', 'num_filters': 32, 'max_pool': 'True', 'num_classes': 100, 'unequal': 0, 'stopping_rounds': 10, 'verbose': 0, 'hold_normalize': 0, 'save_path': '../save/checkpoint\\fedopt_frac0.02', 'exp_folder': 'fedopt_frac0.02', 'resume': None, 'lr_decay': 1}
INFO:root:ResNet(
  (conv1): Conv2d_stand(3, 64, kernel_size=(7, 7), stride=(2, 2), padding=(3, 3), bias=False)
  (bn1): GroupNorm2d(2, eps=1e-05, momentum=0.1, affine=True, track_running_stats=False)
  (relu): ReLU(inplace=True)
  (maxpool): MaxPool2d(kernel_size=3, stride=2, padding=1, dilation=1, ceil_mode=False)
  (layer1): Sequential(
    (0): BasicBlock(
      (conv1): Conv2d_stand(64, 64, kernel_size=(3, 3), stride=(1, 1), padding=(

num_channels_per_group:32
num_channels_per_group:32
num_channels_per_group:32
num_channels_per_group:32
num_channels_per_group:32
num_channels_per_group:64
num_channels_per_group:64
num_channels_per_group:64
num_channels_per_group:64
num_channels_per_group:64
num_channels_per_group:128
num_channels_per_group:128
num_channels_per_group:128
num_channels_per_group:128
num_channels_per_group:128
num_channels_per_group:256
num_channels_per_group:256
num_channels_per_group:256
num_channels_per_group:256
num_channels_per_group:256


  0%|                                                                                         | 0/4000 [00:00<?, ?it/s]INFO:root: 
Avg Training Stats after 1 global rounds:
INFO:root:Training Loss : 15.910684480667111
INFO:root:Train Accuracy: 1.00% 

  0%|                                                                               | 1/4000 [00:03<3:27:48,  3.12s/it]INFO:root: 
Avg Training Stats after 2 global rounds:
INFO:root:Training Loss : 4.463003273010253
INFO:root:Train Accuracy: 0.96% 

  0%|                                                                               | 2/4000 [00:06<3:24:59,  3.08s/it]INFO:root: 
Avg Training Stats after 3 global rounds:
INFO:root:Training Loss : 4.4943335914611815
INFO:root:Train Accuracy: 0.96% 

  0%|                                                                               | 3/4000 [00:09<3:23:19,  3.05s/it]INFO:root: 
Avg Training Stats after 4 global rounds:
INFO:root:Training Loss : 4.477032380104065
INFO:root:Train Accuracy: 1.

INFO:root:Training Loss : 4.408073148727417
INFO:root:Train Accuracy: 1.11% 

  1%|▋                                                                             | 33/4000 [01:40<3:19:18,  3.01s/it]INFO:root: 
Avg Training Stats after 34 global rounds:
INFO:root:Training Loss : 4.481400899887085
INFO:root:Train Accuracy: 1.11% 

  1%|▋                                                                             | 34/4000 [01:43<3:18:56,  3.01s/it]INFO:root: 
Avg Training Stats after 35 global rounds:
INFO:root:Training Loss : 4.468269844055175
INFO:root:Train Accuracy: 1.11% 

  1%|▋                                                                             | 35/4000 [01:46<3:18:45,  3.01s/it]INFO:root: 
Avg Training Stats after 36 global rounds:
INFO:root:Training Loss : 4.5029913568496704
INFO:root:Train Accuracy: 1.11% 

  1%|▋                                                                             | 36/4000 [01:49<3:18:27,  3.00s/it]INFO:root: 
Avg Training Stats after 37 global

  2%|█▎                                                                            | 65/4000 [03:16<3:18:06,  3.02s/it]INFO:root: 
Avg Training Stats after 66 global rounds:
INFO:root:Training Loss : 4.398068017959595
INFO:root:Train Accuracy: 0.74% 

  2%|█▎                                                                            | 66/4000 [03:19<3:18:00,  3.02s/it]INFO:root: 
Avg Training Stats after 67 global rounds:
INFO:root:Training Loss : 4.472428774833679
INFO:root:Train Accuracy: 0.74% 

  2%|█▎                                                                            | 67/4000 [03:22<3:17:58,  3.02s/it]INFO:root: 
Avg Training Stats after 68 global rounds:
INFO:root:Training Loss : 4.469601907730102
INFO:root:Train Accuracy: 0.74% 

  2%|█▎                                                                            | 68/4000 [03:26<3:17:54,  3.02s/it]INFO:root: 
Avg Training Stats after 69 global rounds:
INFO:root:Training Loss : 4.450443463325501
INFO:root:Train Accuracy: 

...

 98%|██████████████████████████████████████████████████████████████████████████▏ | 3906/4000 [4:28:34<09:11,  5.87s/it]INFO:root: 
Avg Training Stats after 3907 global rounds:
INFO:root:Training Loss : 4.44838397026062
INFO:root:Train Accuracy: 0.72% 

 98%|██████████████████████████████████████████████████████████████████████████▏ | 3907/4000 [4:28:40<09:10,  5.92s/it]INFO:root: 
Avg Training Stats after 3908 global rounds:
INFO:root:Training Loss : 4.503570013046264
INFO:root:Train Accuracy: 0.72% 

 98%|██████████████████████████████████████████████████████████████████████████▎ | 3908/4000 [4:28:46<08:59,  5.86s/it]INFO:root: 
Avg Training Stats after 3909 global rounds:
INFO:root:Training Loss : 4.451444468498229
INFO:root:Train Accuracy: 0.72% 

 98%|██████████████████████████████████████████████████████████████████████████▎ | 3909/4000 [4:28:51<08:54,  5.87s/it]INFO:root: 
Avg Training Stats after 3910 global rounds:
INFO:root:Training Loss : 4.499395861625671
INFO:root:Train Acc

 98%|██████████████████████████████████████████████████████████████████████████▊ | 3938/4000 [4:31:39<06:01,  5.83s/it]INFO:root: 
Avg Training Stats after 3939 global rounds:
INFO:root:Training Loss : 4.475029611587524
INFO:root:Train Accuracy: 0.95% 

 98%|██████████████████████████████████████████████████████████████████████████▊ | 3939/4000 [4:31:45<06:00,  5.90s/it]INFO:root: 
Avg Training Stats after 3940 global rounds:
INFO:root:Training Loss : 4.460110130310059
INFO:root:Train Accuracy: 0.78% 

 98%|██████████████████████████████████████████████████████████████████████████▊ | 3940/4000 [4:31:50<05:46,  5.77s/it]INFO:root: 
Avg Training Stats after 3941 global rounds:
INFO:root:Training Loss : 4.486201457977295
INFO:root:Train Accuracy: 0.78% 

 99%|██████████████████████████████████████████████████████████████████████████▉ | 3941/4000 [4:31:56<05:42,  5.80s/it]INFO:root: 
Avg Training Stats after 3942 global rounds:
INFO:root:Training Loss : 4.452706170082092
INFO:root:Train Ac

 99%|███████████████████████████████████████████████████████████████████████████▍| 3970/4000 [4:34:47<02:56,  5.88s/it]INFO:root: 
Avg Training Stats after 3971 global rounds:
INFO:root:Training Loss : 4.474641895294189
INFO:root:Train Accuracy: 1.21% 

 99%|███████████████████████████████████████████████████████████████████████████▍| 3971/4000 [4:34:52<02:50,  5.87s/it]INFO:root: 
Avg Training Stats after 3972 global rounds:
INFO:root:Training Loss : 4.428265933990478
INFO:root:Train Accuracy: 0.34% 

 99%|███████████████████████████████████████████████████████████████████████████▍| 3972/4000 [4:34:58<02:44,  5.88s/it]INFO:root: 
Avg Training Stats after 3973 global rounds:
INFO:root:Training Loss : 4.468158340454102
INFO:root:Train Accuracy: 1.21% 

 99%|███████████████████████████████████████████████████████████████████████████▍| 3973/4000 [4:35:04<02:38,  5.88s/it]INFO:root: 
Avg Training Stats after 3974 global rounds:
INFO:root:Training Loss : 4.446628670692444
INFO:root:Train Ac

 Saving checkpoints to ../save/checkpoint\fedopt_frac0.02\cifar100_resnet18_ws_T[4000]_C[0.02]_iid[2]_E[1]_B[20]...


INFO:root: 
 Results after 4000 global rounds of training:
INFO:root:|---- Test Accuracy: 0.95%


## ws+gn+clip lr 1

In [6]:
args = easydict.EasyDict({
    "model": 'resnet18_ws',
    'dataset': 'cifar100',
    'gpu': 0,
    'iid': 2,
    'epochs': 4000,
    'optimizer': 'clip',
    'seed': 0,
    'norm': 'group_norm',
    'num_users': 500,
    'frac': 0.02,
    'local_ep': 1,
    'local_bs': 20,
    'lr': 1,
    'momentum': 0,
    'kernel_num': 9,
    'kernel_sizes': '3,4,5',
    'num_channnels': '1',
    'num_filters': 32,
    'max_pool': 'True',
    'num_classes': 100,
    'unequal': 0,
    'stopping_rounds': 10,
    'verbose': 0,
    'hold_normalize': 0,
    'save_path': '../save/checkpoint',
    'exp_folder': 'fedopt_frac0.02',
    'resume': None,
    'lr_decay': 1
})

loss_list[3], val_acc_list[3], batch_loss_list[3], conv_grad_list[3], fc_grad_list[3], total_grad_list[3] = main_test(args)

INFO:root:{'model': 'resnet18_ws', 'dataset': 'cifar100', 'gpu': 0, 'iid': 2, 'epochs': 4000, 'optimizer': 'clip', 'seed': 0, 'norm': 'group_norm', 'num_users': 500, 'frac': 0.02, 'local_ep': 1, 'local_bs': 20, 'lr': 1, 'momentum': 0, 'kernel_num': 9, 'kernel_sizes': '3,4,5', 'num_channnels': '1', 'num_filters': 32, 'max_pool': 'True', 'num_classes': 100, 'unequal': 0, 'stopping_rounds': 10, 'verbose': 0, 'hold_normalize': 0, 'save_path': '../save/checkpoint\\fedopt_frac0.02', 'exp_folder': 'fedopt_frac0.02', 'resume': None, 'lr_decay': 1}
INFO:root:ResNet(
  (conv1): Conv2d_stand(3, 64, kernel_size=(7, 7), stride=(2, 2), padding=(3, 3), bias=False)
  (bn1): GroupNorm2d(2, eps=1e-05, momentum=0.1, affine=True, track_running_stats=False)
  (relu): ReLU(inplace=True)
  (maxpool): MaxPool2d(kernel_size=3, stride=2, padding=1, dilation=1, ceil_mode=False)
  (layer1): Sequential(
    (0): BasicBlock(
      (conv1): Conv2d_stand(64, 64, kernel_size=(3, 3), stride=(1, 1), padding=(1, 1), bias

num_channels_per_group:32
num_channels_per_group:32
num_channels_per_group:32
num_channels_per_group:32
num_channels_per_group:32
num_channels_per_group:64
num_channels_per_group:64
num_channels_per_group:64
num_channels_per_group:64
num_channels_per_group:64
num_channels_per_group:128
num_channels_per_group:128
num_channels_per_group:128
num_channels_per_group:128
num_channels_per_group:128
num_channels_per_group:256
num_channels_per_group:256
num_channels_per_group:256
num_channels_per_group:256
num_channels_per_group:256


  0%|                                                                                         | 0/4000 [00:00<?, ?it/s]INFO:root: 
Avg Training Stats after 1 global rounds:
INFO:root:Training Loss : 4.107586255073548
INFO:root:Train Accuracy: 0.78% 

  0%|                                                                               | 1/4000 [00:03<3:44:39,  3.37s/it]INFO:root: 
Avg Training Stats after 2 global rounds:
INFO:root:Training Loss : 4.05429470539093
INFO:root:Train Accuracy: 1.14% 

  0%|                                                                               | 2/4000 [00:06<3:40:38,  3.31s/it]INFO:root: 
Avg Training Stats after 3 global rounds:
INFO:root:Training Loss : 4.044192790985107
INFO:root:Train Accuracy: 1.06% 

  0%|                                                                               | 3/4000 [00:09<3:38:04,  3.27s/it]INFO:root: 
Avg Training Stats after 4 global rounds:
INFO:root:Training Loss : 3.9571920776367184
INFO:root:Train Accuracy: 1.35

INFO:root:Training Loss : 3.5644617271423344
INFO:root:Train Accuracy: 3.58% 

  1%|▋                                                                             | 33/4000 [01:51<4:09:52,  3.78s/it]INFO:root: 
Avg Training Stats after 34 global rounds:
INFO:root:Training Loss : 3.7460479736328125
INFO:root:Train Accuracy: 4.09% 

  1%|▋                                                                             | 34/4000 [01:54<4:00:14,  3.63s/it]INFO:root: 
Avg Training Stats after 35 global rounds:
INFO:root:Training Loss : 3.6623609352111814
INFO:root:Train Accuracy: 4.11% 

  1%|▋                                                                             | 35/4000 [01:57<3:52:14,  3.51s/it]INFO:root: 
Avg Training Stats after 36 global rounds:
INFO:root:Training Loss : 3.5763738465309145
INFO:root:Train Accuracy: 4.43% 

  1%|▋                                                                             | 36/4000 [02:00<3:46:26,  3.43s/it]INFO:root: 
Avg Training Stats after 37 glo

  2%|█▎                                                                            | 65/4000 [03:35<3:35:11,  3.28s/it]INFO:root: 
Avg Training Stats after 66 global rounds:
INFO:root:Training Loss : 3.2728649163246155
INFO:root:Train Accuracy: 7.88% 

  2%|█▎                                                                            | 66/4000 [03:38<3:35:31,  3.29s/it]INFO:root: 
Avg Training Stats after 67 global rounds:
INFO:root:Training Loss : 3.3846587228775027
INFO:root:Train Accuracy: 7.51% 

  2%|█▎                                                                            | 67/4000 [03:41<3:34:57,  3.28s/it]INFO:root: 
Avg Training Stats after 68 global rounds:
INFO:root:Training Loss : 3.399427518844605
INFO:root:Train Accuracy: 8.09% 

  2%|█▎                                                                            | 68/4000 [03:45<3:34:58,  3.28s/it]INFO:root: 
Avg Training Stats after 69 global rounds:
INFO:root:Training Loss : 3.4018748188018804
INFO:root:Train Accurac

...

INFO:root:Train Accuracy: 27.93% 

 58%|██████████████████████████████████████████▋                               | 2305/4000 [2:23:21<2:05:29,  4.44s/it]INFO:root: 
Avg Training Stats after 2306 global rounds:
INFO:root:Training Loss : 0.06811407249726473
INFO:root:Train Accuracy: 28.04% 

 58%|██████████████████████████████████████████▋                               | 2306/4000 [2:23:25<2:08:08,  4.54s/it]INFO:root: 
Avg Training Stats after 2307 global rounds:
INFO:root:Training Loss : 0.05905556921934476
INFO:root:Train Accuracy: 27.92% 

 58%|██████████████████████████████████████████▋                               | 2307/4000 [2:23:30<2:08:01,  4.54s/it]INFO:root: 
Avg Training Stats after 2308 global rounds:
INFO:root:Training Loss : 0.02891250022890745
INFO:root:Train Accuracy: 27.76% 

 58%|██████████████████████████████████████████▋                               | 2308/4000 [2:23:35<2:07:41,  4.53s/it]INFO:root: 
Avg Training Stats after 2309 global rounds:
INFO:root:Training

INFO:root:Train Accuracy: 27.72% 

 58%|███████████████████████████████████████████▏                              | 2337/4000 [2:25:42<2:02:19,  4.41s/it]INFO:root: 
Avg Training Stats after 2338 global rounds:
INFO:root:Training Loss : 0.03972530335959164
INFO:root:Train Accuracy: 27.80% 

 58%|███████████████████████████████████████████▎                              | 2338/4000 [2:25:46<2:02:19,  4.42s/it]INFO:root: 
Avg Training Stats after 2339 global rounds:
INFO:root:Training Loss : 0.037116753893205894
INFO:root:Train Accuracy: 27.76% 

 58%|███████████████████████████████████████████▎                              | 2339/4000 [2:25:51<2:02:35,  4.43s/it]INFO:root: 
Avg Training Stats after 2340 global rounds:
INFO:root:Training Loss : 0.013869231975695584
INFO:root:Train Accuracy: 27.66% 

 58%|███████████████████████████████████████████▎                              | 2340/4000 [2:25:55<2:02:51,  4.44s/it]INFO:root: 
Avg Training Stats after 2341 global rounds:
INFO:root:Traini

INFO:root:Train Accuracy: 27.33% 

 59%|███████████████████████████████████████████▊                              | 2369/4000 [2:28:04<2:01:21,  4.46s/it]INFO:root: 
Avg Training Stats after 2370 global rounds:
INFO:root:Training Loss : 0.040902461155928896
INFO:root:Train Accuracy: 27.60% 

 59%|███████████████████████████████████████████▊                              | 2370/4000 [2:28:09<2:01:49,  4.48s/it]INFO:root: 
Avg Training Stats after 2371 global rounds:
INFO:root:Training Loss : 0.037020997996442026
INFO:root:Train Accuracy: 27.55% 

 59%|███████████████████████████████████████████▊                              | 2371/4000 [2:28:13<2:01:08,  4.46s/it]INFO:root: 
Avg Training Stats after 2372 global rounds:
INFO:root:Training Loss : 0.0806497979775304
INFO:root:Train Accuracy: 27.35% 

 59%|███████████████████████████████████████████▉                              | 2372/4000 [2:28:18<2:01:30,  4.48s/it]INFO:root: 
Avg Training Stats after 2373 global rounds:
INFO:root:Trainin

INFO:root:Train Accuracy: 27.01% 

 60%|████████████████████████████████████████████▍                             | 2401/4000 [2:30:28<2:02:50,  4.61s/it]INFO:root: 
Avg Training Stats after 2402 global rounds:
INFO:root:Training Loss : 0.06908622067441685
INFO:root:Train Accuracy: 27.64% 

 60%|████████████████████████████████████████████▍                             | 2402/4000 [2:30:32<2:00:44,  4.53s/it]INFO:root: 
Avg Training Stats after 2403 global rounds:
INFO:root:Training Loss : 0.18780657251569208
INFO:root:Train Accuracy: 27.46% 

 60%|████████████████████████████████████████████▍                             | 2403/4000 [2:30:36<1:59:43,  4.50s/it]INFO:root: 
Avg Training Stats after 2404 global rounds:
INFO:root:Training Loss : 0.05058321473465185
INFO:root:Train Accuracy: 27.55% 

 60%|████████████████████████████████████████████▍                             | 2404/4000 [2:30:41<1:58:43,  4.46s/it]INFO:root: 
Avg Training Stats after 2405 global rounds:
INFO:root:Training

KeyboardInterrupt: 

## ws+gn+clip lr 5

In [ ]:
args = easydict.EasyDict({
    "model": 'resnet18',
    'dataset': 'cifar100',
    'gpu': 0,
    'iid': 2,
    'epochs': 4000,
    'optimizer': 'clip',
    'seed': 0,
    'norm': 'group_norm',
    'num_users': 500,
    'frac': 0.02,
    'local_ep': 1,
    'local_bs': 20,
    'lr': 5,
    'momentum': 0,
    'kernel_num': 9,
    'kernel_sizes': '3,4,5',
    'num_channnels': '1',
    'num_filters': 32,
    'max_pool': 'True',
    'num_classes': 100,
    'unequal': 0,
    'stopping_rounds': 10,
    'verbose': 0,
    'hold_normalize': 0,
    'save_path': '../save/checkpoint',
    'exp_folder': 'fedopt_frac0.02',
    'resume': None,
    'lr_decay': 1
})

loss_list[4], val_acc_list[4], batch_loss_list[4], conv_grad_list[4], fc_grad_list[4], total_grad_list[4] = main_test(args)

## ws+gn lr 0.1

In [ ]:
args = easydict.EasyDict({
    "model": 'resnet18',
    'dataset': 'cifar100',
    'gpu': 0,
    'iid': 2,
    'epochs': 4000,
    'optimizer': 'no_weight_decay',
    'seed': 0,
    'norm': 'group_norm',
    'num_users': 500,
    'frac': 0.02,
    'local_ep': 1,
    'local_bs': 20,
    'lr': 0.1,
    'momentum': 0,
    'kernel_num': 9,
    'kernel_sizes': '3,4,5',
    'num_channnels': '1',
    'num_filters': 32,
    'max_pool': 'True',
    'num_classes': 100,
    'unequal': 0,
    'stopping_rounds': 10,
    'verbose': 0,
    'hold_normalize': 0,
    'save_path': '../save/checkpoint',
    'exp_folder': 'fedopt_frac0.02',
    'resume': None,
    'lr_decay': 1
})

loss_list[5], val_acc_list[5], batch_loss_list[5], conv_grad_list[5], fc_grad_list[5], total_grad_list[5] = main_test(args)